<a href="https://colab.research.google.com/github/victorsmoreschi/Easy-or-Really-Easy-Data-Studies/blob/main/Winning_Jeopardy.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Introduction

Jeopardy is a popular TV show in the US where participants answer questions to win money. It's been running for many years, and is a major force in popular culture.

Imagine that you want to compete on Jeopardy, and you're looking for any way to win.

The dataset is named jeopardy.csv, and contains 20000 rows from the beginning of a full dataset of Jeopardy questions, which you can download [here](https://www.reddit.com/r/datasets/comments/1uyd0t/200000_jeopardy_questions_in_a_json_file/).

In [2]:
import pandas as pd
import numpy as np
import scipy.stats

In [3]:
df = pd.read_json('/content/drive/MyDrive/Colab Notebooks/JEOPARDY_QUESTIONS1.json')

In [4]:
df.head(3)

category    air_date  \
0                          HISTORY  2004-12-31   
1  ESPN's TOP 10 ALL-TIME ATHLETES  2004-12-31   
2      EVERYBODY TALKS ABOUT IT...  2004-12-31   

                                            question value      answer  \
0  'For the last 8 years of his life, Galileo was...  $200  Copernicus   
1  'No. 2: 1912 Olympian; football star at Carlis...  $200  Jim Thorpe   
2  'The city of Yuma in this state has a record a...  $200     Arizona   

       round  show_number  
0  Jeopardy!         4680  
1  Jeopardy!         4680  
2  Jeopardy!         4680

## Data Cleaning

In [5]:
# Some of the column names have spaces in front
correct_columns = []
for i in df.columns:
  correct_columns.append(i.replace(' ', ''))

df.columns = correct_columns

In [6]:
# adjust column types
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 216930 entries, 0 to 216929
Data columns (total 7 columns):
 #   Column       Non-Null Count   Dtype 
---  ------       --------------   ----- 
 0   category     216930 non-null  object
 1   air_date     216930 non-null  object
 2   question     216930 non-null  object
 3   value        213296 non-null  object
 4   answer       216930 non-null  object
 5   round        216930 non-null  object
 6   show_number  216930 non-null  int64 
dtypes: int64(1), object(6)
memory usage: 11.6+ MB


In [7]:
df['value'] = df['value'].str.replace('$', '').str.replace(',','').astype(float)

In [8]:
df['air_date'] = pd.to_datetime(df['air_date'])

In [9]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 216930 entries, 0 to 216929
Data columns (total 7 columns):
 #   Column       Non-Null Count   Dtype         
---  ------       --------------   -----         
 0   category     216930 non-null  object        
 1   air_date     216930 non-null  datetime64[ns]
 2   question     216930 non-null  object        
 3   value        213296 non-null  float64       
 4   answer       216930 non-null  object        
 5   round        216930 non-null  object        
 6   show_number  216930 non-null  int64         
dtypes: datetime64[ns](1), float64(1), int64(1), object(4)
memory usage: 11.6+ MB


In [10]:
# Normalize strings so it s possible to do an analysis on each word
def normalize_string(string):
  string = string.str.lower()
  string = string.str.replace('[^\w\s]', '')
  return string

In [11]:
df['clean_question'] = normalize_string(df['question'])
df['clean_answer'] = normalize_string(df['answer'])

## Testing Hypothesis

In [37]:
# Investigate if the answers appear in the question
def q_a(series):
  split_answer = series['clean_answer'].split()
  split_question = series['clean_question'].split()

  match_count = 0
  if 'the' in split_answer:
    split_answer.remove('the')
  if len(split_answer) == 0:
    return 0
  for i in split_answer:
    if i in split_question:
      match_count += 1
  return match_count / len(split_answer)


In [13]:
df['answer_in_question'] = df.apply(q_a, axis=1)
df['answer_in_question'].mean()

0.035895718003208635

In [14]:
df.head(5)

category   air_date  \
0                          HISTORY 2004-12-31   
1  ESPN's TOP 10 ALL-TIME ATHLETES 2004-12-31   
2      EVERYBODY TALKS ABOUT IT... 2004-12-31   
3                 THE COMPANY LINE 2004-12-31   
4              EPITAPHS & TRIBUTES 2004-12-31   

                                            question  value       answer  \
0  'For the last 8 years of his life, Galileo was...  200.0   Copernicus   
1  'No. 2: 1912 Olympian; football star at Carlis...  200.0   Jim Thorpe   
2  'The city of Yuma in this state has a record a...  200.0      Arizona   
3  'In 1963, live on "The Art Linkletter Show", t...  200.0  McDonald\'s   
4  'Signer of the Dec. of Indep., framer of the C...  200.0   John Adams   

       round  show_number                                     clean_question  \
0  Jeopardy!         4680  'for the last 8 years of his life, galileo was...   
1  Jeopardy!         4680  'no. 2: 1912 olympian; football star at carlis...   
2  Jeopardy!         4680  'the city of yuma in this state has a record a...   
3  Jeopardy!         4680  'in 1963, live on "the art linkletter show", t...   
4  Jeopardy!         4680  'signer of the dec. of indep., framer of the c...   

  clean_answer  answer_in_question  
0   copernicus                 0.0  
1   jim thorpe                 0.0  
2      arizona                 0.0  
3  mcdonald\'s                 0.0  
4   john adams                 0.0

Only 3.5% of the answers are mentioned in the question. This mean is not an effective strategy.

In [15]:
# investigate how often new questions are repeats of older ones

question_overlap = []
terms_used = set()
df = df.sort_values('air_date')
for index, row in df.iterrows():
  split_question = row['clean_question'].split()
  split_question = [q for q in split_question if len(q) > 5]
  match_count = 0

  for word in split_question:
    if word in terms_used:
      match_count += 1
  for word in split_question:
    terms_used.add(word)
  if len(split_question) > 0:
    question_overlap.append(match_count / len(split_question))
  else:
    question_overlap.append(0)


df['question_overlap'] = question_overlap

df['question_overlap'].mean()

0.774594287590915

There is about a 77% overlap between terms in new questions and terms in old questions. This only looks at a small set of questions, and it doesn't look at phrases — it looks at single terms. This makes it relatively significant, it's worth looking more into the recycling of questions.

Just assuming words with less then 6 characters are not valuable for the analysis may not be the most accurate measure. So now **I will try the same, but removing words that are in more the 5% of the question, because those are probably not specific question words.**

In [16]:
# Creating a dict to count each time each word appears
questions_splited = [q.split() for q in df['clean_question']]
word_count = {}
total_words = 0
for question in questions_splited:
  for word in question:
    total_words += 1
    if word in word_count:
      word_count[word] += 1
    else:
      word_count[word] = 1

In [17]:
# Divide each word count to the total number of word to see the representativity
percentual_word_count = {}
for word in word_count:
  percentual_word_count[word] = word_count[word] / total_words
print(max(percentual_word_count, key=percentual_word_count.get))
percentual_word_count['the']

the


0.04721893011618602

Apparently, the word that is most representative is `the` and still just represents 4.7% of the word population. So, I will filter for words that represent less then 1%

In [18]:
# Same code as cell above
question_overlap2 = []
terms_used = set()

for index, row in df.iterrows():
  split_question = row['clean_question'].split()
  split_question = [q for q in split_question if percentual_word_count[q] < 0.01]
  match_count = 0

  for word in split_question:
    if word in terms_used:
      match_count += 1
  for word in split_question:
    terms_used.add(word)
  if len(split_question) > 0:
    question_overlap2.append(match_count / len(split_question))
  else:
    question_overlap2.append(0)


df['question_overlap2'] = question_overlap2

df['question_overlap2'].mean()

0.871397541313318

Doing a better filter, **there is about a 87% overlap between terms in new questions and terms in old questions**. This only looks at a small set of questions, and it doesn't look at phrases — it looks at single terms. This makes it relatively significant, it's worth looking more into the recycling of questions.

Below, I study questions that pertain to high value or low value questions to see if there is a relation between terms and th value of the question.

In [19]:
def value_questions(row):

  if row['value'] > 800:
    value = 1
  else:
    value = 0
  return value

In [20]:
df['high_value'] = df.apply(value_questions, axis=1)

In [21]:
def count_usage(term):
  low_count = 0
  high_count = 0
  for index, row in df.iterrows():
    split_question = row['clean_question'].split()
    if term in split_question:
      if row['high_value'] == 1:
        high_count += 1
      else:
        low_count += 1
  return high_count, low_count

In [22]:
import numpy as np
import scipy.stats

# Assuming terms_used is already defined
comparison_terms = [np.random.choice(list(terms_used)) for _ in range(10)]

observed_expected = []

# Count usage for each term
for term in comparison_terms:
    observed_expected.append(count_usage(term))

# High and low value counts
high_value_count = df[df['high_value'] == 1].shape[0]
low_value_count = df[df['high_value'] == 0].shape[0]

# Chi-square calculation
chi_squared = []
for obs in observed_expected:
    total = sum(obs)
    total_prop = total / df.shape[0]
    high_value_exp = total_prop * high_value_count
    low_value_exp = total_prop * low_value_count

    # Using numpy arrays for observed and expected values
    observed = np.array([obs[0], obs[1]])
    expected = np.array([high_value_exp, low_value_exp])
    chi_squared.append(scipy.stats.chisquare(observed, expected))

print(chi_squared)


[Power_divergenceResult(statistic=2.5317964247338085, pvalue=0.11157312838169751), Power_divergenceResult(statistic=0.3949764642333513, pvalue=0.5296950912486695), Power_divergenceResult(statistic=0.3949764642333513, pvalue=0.5296950912486695), Power_divergenceResult(statistic=2.5317964247338085, pvalue=0.11157312838169751), Power_divergenceResult(statistic=0.46338644448358013, pvalue=0.49604555208958945), Power_divergenceResult(statistic=2.5317964247338085, pvalue=0.11157312838169751), Power_divergenceResult(statistic=0.07446818777814278, pvalue=0.7849388502668134), Power_divergenceResult(statistic=0.021646150708492677, pvalue=0.8830323245068887), Power_divergenceResult(statistic=0.3949764642333513, pvalue=0.5296950912486695), Power_divergenceResult(statistic=2.5317964247338085, pvalue=0.11157312838169751)]


None of the terms had a significant difference in usage between high value and low value rows. Additionally, the frequencies were all lower than 5, so the chi-squared test isn't as valid. It would be better to run this test with only terms that have higher frequencies.

In [23]:
observed_expected

[(1, 0),
 (0, 1),
 (0, 1),
 (1, 0),
 (1, 1),
 (1, 0),
 (2, 4),
 (1, 3),
 (0, 1),
 (1, 0)]

### The Category Column

Taking a close look to:
* See which categories appear the most often.
* Find the probability of each category appearing in each round.

In [24]:
df['category'].value_counts()

category
BEFORE & AFTER                 547
SCIENCE                        519
LITERATURE                     496
AMERICAN HISTORY               418
POTPOURRI                      401
                              ... 
HISTORIC CANADIAN GEOGRAPHY      1
MIDWEST TOPOGRAPHY               1
CLASSIC MOVIES & TELEVISION      1
CURRENT ROYALTY                  1
WRITER/DIRECTORS                 1
Name: count, Length: 27995, dtype: int64

In [25]:
df['round'].value_counts()

round
Jeopardy!           107384
Double Jeopardy!    105912
Final Jeopardy!       3631
Tiebreaker               3
Name: count, dtype: int64

In [26]:
grouped_df = df.groupby('round')['category'].value_counts().unstack(fill_value=0)
grouped_df

category           A JIM CARREY FILM FESTIVAL  "!"  "-ARES"  \
round                                                         
Double Jeopardy!                            0    0        5   
Final Jeopardy!                             0    0        0   
Jeopardy!                                   5    5        0   
Tiebreaker                                  0    0        0   

category          "-ICIAN" EXPEDITION  "...OD" WORDS  "1", "2", "3"  \
round                                                                 
Double Jeopardy!                    0              5              5   
Final Jeopardy!                     0              0              0   
Jeopardy!                           5              0              0   
Tiebreaker                          0              0              0   

category          "20" QUESTIONS  "A" & "E"  "A" & "M"  "A" + 4  ...  “CC”  \
round                                                            ...         
Double Jeopardy!               5          0          0        5  ...     0   
Final Jeopardy!                0          0          0        0  ...     0   
Jeopardy!                      0          5          5        0  ...     5   
Tiebreaker                     0          0          0        0  ...     0   

category          “GUT”s  “G” WHIZ!  “HARD” & “EASY” MOVIES  “NORTH”  \
round                                                                  
Double Jeopardy!       5          0                       5        0   
Final Jeopardy!        0          0                       0        0   
Jeopardy!              0          5                       0        5   
Tiebreaker             0          0                       0        0   

category          “R” MOVIES  “SAINTS”  “SOUTH”  “STREETS”  “WH”AT IS IT?  
round                                                                      
Double Jeopardy!           5         4        5          0              5  
Final Jeopardy!            0         0        0          0              0  
Jeopardy!                  0         0        0          5              0  
Tiebreaker                 0         0        0          0              0  

[4 rows x 27995 columns]

In [27]:
grouped_df_proportions = grouped_df.div(grouped_df.sum(axis=1), axis=0)
grouped_df_proportions

category           A JIM CARREY FILM FESTIVAL       "!"   "-ARES"  \
round                                                               
Double Jeopardy!                     0.000000  0.000000  0.000047   
Final Jeopardy!                      0.000000  0.000000  0.000000   
Jeopardy!                            0.000047  0.000047  0.000000   
Tiebreaker                           0.000000  0.000000  0.000000   

category          "-ICIAN" EXPEDITION  "...OD" WORDS  "1", "2", "3"  \
round                                                                 
Double Jeopardy!             0.000000       0.000047       0.000047   
Final Jeopardy!              0.000000       0.000000       0.000000   
Jeopardy!                    0.000047       0.000000       0.000000   
Tiebreaker                   0.000000       0.000000       0.000000   

category          "20" QUESTIONS  "A" & "E"  "A" & "M"   "A" + 4  ...  \
round                                                             ...   
Double Jeopardy!        0.000047   0.000000   0.000000  0.000047  ...   
Final Jeopardy!         0.000000   0.000000   0.000000  0.000000  ...   
Jeopardy!               0.000000   0.000047   0.000047  0.000000  ...   
Tiebreaker              0.000000   0.000000   0.000000  0.000000  ...   

category              “CC”    “GUT”s  “G” WHIZ!  “HARD” & “EASY” MOVIES  \
round                                                                     
Double Jeopardy!  0.000000  0.000047   0.000000                0.000047   
Final Jeopardy!   0.000000  0.000000   0.000000                0.000000   
Jeopardy!         0.000047  0.000000   0.000047                0.000000   
Tiebreaker        0.000000  0.000000   0.000000                0.000000   

category           “NORTH”  “R” MOVIES  “SAINTS”   “SOUTH”  “STREETS”  \
round                                                                   
Double Jeopardy!  0.000000    0.000047  0.000038  0.000047   0.000000   
Final Jeopardy!   0.000000    0.000000  0.000000  0.000000   0.000000   
Jeopardy!         0.000047    0.000000  0.000000  0.000000   0.000047   
Tiebreaker        0.000000    0.000000  0.000000  0.000000   0.000000   

category          “WH”AT IS IT?  
round                            
Double Jeopardy!       0.000047  
Final Jeopardy!        0.000000  
Jeopardy!              0.000000  
Tiebreaker             0.000000  

[4 rows x 27995 columns]

In [28]:
from IPython.display import display, HTML
display(HTML(grouped_df_proportions.to_html()))

In [33]:
top_5_categories = grouped_df_proportions.apply(lambda x: x.nlargest(5).index, axis=1)
print(top_5_categories)

round
Double Jeopardy!    Index(['BEFORE & AFTER', 'LITERATURE', 'SCIENC...
Final Jeopardy!     Index(['U.S. PRESIDENTS', 'WORD ORIGINS', 'STA...
Jeopardy!           Index(['POTPOURRI', 'STUPID ANSWERS', 'SPORTS'...
Tiebreaker          Index(['CHILD'S PLAY', 'LITERARY CHARACTERS', ...
dtype: object


In [36]:
grouped_df_sorted = grouped_df_proportions.apply(lambda x: x.sort_values(ascending=False).head(5), axis=1).fillna(0)
grouped_df_sorted

category           A JIM CARREY FILM FESTIVAL  AMERICAN HISTORY  ANIMALS  \
round                                                                      
Double Jeopardy!                          0.0          0.000000  0.00000   
Final Jeopardy!                           0.0          0.000000  0.00000   
Jeopardy!                                 0.0          0.002114  0.00217   
Tiebreaker                                0.0          0.000000  0.00000   

category           AUTHORS  BEFORE & AFTER  CHILD'S PLAY  LITERARY CHARACTERS  \
round                                                                           
Double Jeopardy!  0.000000        0.004249      0.000000             0.000000   
Final Jeopardy!   0.007436        0.000000      0.000000             0.000000   
Jeopardy!         0.000000        0.000000      0.000000             0.000000   
Tiebreaker        0.000000        0.000000      0.333333             0.333333   

category          LITERATURE    OPERA  POTPOURRI  PRESIDENTIAL MOMS   SCIENCE  \
round                                                                           
Double Jeopardy!    0.003597  0.00236   0.000000                0.0  0.002795   
Final Jeopardy!     0.000000  0.00000   0.000000                0.0  0.000000   
Jeopardy!           0.000000  0.00000   0.002375                0.0  0.000000   
Tiebreaker          0.000000  0.00000   0.000000                0.0  0.000000   

category            SPORTS  STATE CAPITALS  STUPID ANSWERS  \
round                                                        
Double Jeopardy!  0.000000        0.000000        0.000000   
Final Jeopardy!   0.000000        0.008538        0.000000   
Jeopardy!         0.002356        0.000000        0.002375   
Tiebreaker        0.000000        0.000000        0.000000   

category          THE AMERICAN REVOLUTION  U.S. PRESIDENTS  WORD ORIGINS  \
round                                                                      
Double Jeopardy!                 0.000000          0.00000      0.000000   
Final Jeopardy!                  0.000000          0.01377      0.009364   
Jeopardy!                        0.000000          0.00000      0.000000   
Tiebreaker                       0.333333          0.00000      0.000000   

category          WORLD GEOGRAPHY  WORLD LEADERS  
round                                             
Double Jeopardy!         0.002398       0.000000  
Final Jeopardy!          0.000000       0.007161  
Jeopardy!                0.000000       0.000000  
Tiebreaker               0.000000       0.000000

Filtering this DF for the categories that appear most often, is possible to see that there isnt a category that has a big relevance for each round. For example, during **Jeopardy! Round**, the category **American History** has the highest probability to appear, **but this probability is 0.2%, which is really small**. To have a better lookout, an analysis should group a lot of categories in bigger categories, but I am not going to do that.